In [5]:
import numpy as np
import os
from typing import List, Dict, Tuple
import pandas as pd
from tqdm.notebook import tqdm

In [23]:
a = np.array([[0, 1]])
np.vstack((a, np.array([0, 0])))

array([[0, 1],
       [0, 0]])

In [34]:
tuple(["lol"])

('lol',)

In [26]:
for e in os.listdir("rnn_tokentype_data/train"):
    print(e)

GreaterManchesterCrime.txt
KaggleDBQA_combined.txt
TheHistoryofBaseball.txt
dataset_tests_pr_60095.txt
GeoNuclearData.txt
Pesticide.txt
spider_train.txt
StudentMathScore.txt
wikisql_train.txt


In [ ]:
class MarkovModel:
    def __init__(self, n: int = 3) -> None:
        self.n = n
        self.tokens2idx: List[Dict[Tuple | str, int]] = [dict() for _ in range(n - 1)]
        self.idx2token: Dict[int, str] = dict()
        self.ngrams_cnt: List[np.ndarray] = [None for _ in range(n)]
    
    def _update_vocab(self, tokens: List[str]) -> None:
        assert len(tokens) == self.n - 1
        for i in range(len(tokens) - 1, -1):
            prev_n = tokens[i:]
            if len(prev_n) != 1:
                prev_n = tuple(prev_n)
            self.tokens2idx
    
    def _update_pair_vocab(self, pair: Tuple[str, str]) -> None:
        if pair in self.pair2idx:
            return
        self.pair2idx[pair] = len(self.pair2idx)
        if self.three_grams_cnt is None:
            self.three_grams_cnt = np.zeros(shape=(1, len(self.token2idx)))
            return
        self.three_grams_cnt = np.vstack((self.three_grams_cnt, np.zeros(self.three_grams_cnt.shape[1])))
    
    def _update_abs_cnt(self, token: str) -> int:
        idx = self.token2idx[token]
        self.abs_cnt[idx] += 1
        return self.abs_cnt[idx]

    def _update_two_grams(self, prev_token: str, cur_token: str) -> int:
        prev_idx: int = self.token2idx[prev_token]
        cur_idx: int = self.token2idx[cur_token]
        self.two_grams_cnt[prev_idx][cur_idx] += 1
        return self.two_grams_cnt[prev_idx][cur_idx]
    
    def _update_three_grams(self, prev_pair: Tuple[str, str], cur_token: str) -> int:
        prev_pair_idx: int = self.pair2idx[prev_pair]
        cur_idx: int = self.token2idx[cur_token]
        self.three_grams_cnt[prev_pair_idx][cur_idx] += 1
        return self.three_grams_cnt[prev_pair_idx][cur_idx]  
    
    def update(self, tokens: List[str]) -> None:
       for i in range(len(tokens)):
            self._update_token_vocab(tokens[i])
            self._update_abs_cnt(tokens[i])
            if i - 1 < 0:
                continue
            self._update_pair_vocab((tokens[i - 1], tokens[i]))
            self._update_two_grams(tokens[i-1], tokens[i])
            if i - 2 < 0:
                continue
            self._update_three_grams((tokens[i - 2], tokens[i - 1]), tokens[i])
    
    def _zero_fallback(self) -> str:
         return self.idx2token[np.argmax(self.abs_cnt)]

    def _one_fallback(self, prev_token: str) -> str:
        if prev_token not in self.token2idx:
            return self._zero_fallback()
        prev_idx = self.token2idx[prev_token]
        two_gram_for_prev = self.two_grams_cnt[prev_idx, :]
        if np.max(two_gram_for_prev) == 0:
            return self._zero_fallback()
        return self.idx2token[np.argmax(two_gram_for_prev)]

    def _two_fallback(self, pair: Tuple[str, str]) -> str:
        if pair not in self.pair2idx:
            return self._one_fallback(pair[-1])
        pair_idx = self.pair2idx[pair]
        three_gram_for_pair = self.three_grams_cnt[pair_idx, :]
        if np.max(three_gram_for_pair) == 0:
            return self._one_fallback(pair[-1])
        two_gram_for_prev = self.two_grams_cnt[self.token2idx[pair[-1]], :]
        probs = two_gram_for_prev + three_gram_for_pair
        return self.idx2token[np.argmax(probs)]
        
    def predict_next(self, tokens: List[str] = []) -> str:
        if len(tokens) == 0:
            return self._zero_fallback()
        if len(tokens) == 1:
            return self._one_fallback(tokens[0])
        
        return self._two_fallback((tokens[-2], tokens[-1]))



    def evaluate(self, path_to_file: str) -> float:
        pass

In [22]:
class MarkovModel:
    def __init__(self) -> None:
        self.pair2idx: Dict[Tuple[str, str], int] = dict()
        self.token2idx: Dict[str, int] = dict()
        self.idx2token: Dict[int, str] = dict()
        self.abs_cnt: np.ndarray = None
        self.two_grams_cnt: np.ndarray = None
        self.three_grams_cnt: np.ndarray = None
    
    def _update_token_vocab(self, token: str) -> None:
        if token in self.token2idx:
            return
        self.token2idx[token] = len(self.token2idx)
        self.idx2token[self.token2idx[token]] = token
        if self.abs_cnt is None:
            self.abs_cnt = np.array([0])
            self.two_grams_cnt = np.array([[0]])
            return
        self.abs_cnt = np.append(self.abs_cnt, [0])
        self.two_grams_cnt = np.c_[self.two_grams_cnt, np.zeros(self.two_grams_cnt.shape[0])]
        self.two_grams_cnt = np.vstack((self.two_grams_cnt, np.zeros(self.two_grams_cnt.shape[1])))
        if self.three_grams_cnt is None:
            return
        self.three_grams_cnt = np.c_[self.three_grams_cnt, np.zeros(self.three_grams_cnt.shape[0])]
    
    def _update_pair_vocab(self, pair: Tuple[str, str]) -> None:
        if pair in self.pair2idx:
            return
        self.pair2idx[pair] = len(self.pair2idx)
        if self.three_grams_cnt is None:
            self.three_grams_cnt = np.zeros(shape=(1, len(self.token2idx)))
            return
        self.three_grams_cnt = np.vstack((self.three_grams_cnt, np.zeros(self.three_grams_cnt.shape[1])))
    
    def _update_abs_cnt(self, token: str) -> int:
        idx = self.token2idx[token]
        self.abs_cnt[idx] += 1
        return self.abs_cnt[idx]

    def _update_two_grams(self, prev_token: str, cur_token: str) -> int:
        prev_idx: int = self.token2idx[prev_token]
        cur_idx: int = self.token2idx[cur_token]
        self.two_grams_cnt[prev_idx][cur_idx] += 1
        return self.two_grams_cnt[prev_idx][cur_idx]
    
    def _update_three_grams(self, prev_pair: Tuple[str, str], cur_token: str) -> int:
        prev_pair_idx: int = self.pair2idx[prev_pair]
        cur_idx: int = self.token2idx[cur_token]
        self.three_grams_cnt[prev_pair_idx][cur_idx] += 1
        return self.three_grams_cnt[prev_pair_idx][cur_idx]  
    
    def update(self, tokens: List[str]) -> None:
       for i in range(len(tokens)):
            self._update_token_vocab(tokens[i])
            self._update_abs_cnt(tokens[i])
            if i - 1 < 0:
                continue
            self._update_pair_vocab((tokens[i - 1], tokens[i]))
            self._update_two_grams(tokens[i-1], tokens[i])
            if i - 2 < 0:
                continue
            self._update_three_grams((tokens[i - 2], tokens[i - 1]), tokens[i])
    
    def _zero_fallback(self) -> str:
         return self.idx2token[np.argmax(self.abs_cnt)]

    def _one_fallback(self, prev_token: str) -> str:
        if prev_token not in self.token2idx:
            return self._zero_fallback()
        prev_idx = self.token2idx[prev_token]
        two_gram_for_prev = self.two_grams_cnt[prev_idx, :]
        if np.max(two_gram_for_prev) == 0:
            return self._zero_fallback()
        return self.idx2token[np.argmax(two_gram_for_prev)]

    def _two_fallback(self, pair: Tuple[str, str]) -> str:
        if pair not in self.pair2idx:
            return self._one_fallback(pair[-1])
        pair_idx = self.pair2idx[pair]
        three_gram_for_pair = self.three_grams_cnt[pair_idx, :]
        if np.max(three_gram_for_pair) == 0:
            return self._one_fallback(pair[-1])
        two_gram_for_prev = self.two_grams_cnt[self.token2idx[pair[-1]], :]
        probs = three_gram_for_pair
        return self.idx2token[np.argmax(probs)]
        
    def predict_next(self, tokens: List[str] = []) -> str:
        if len(tokens) == 0:
            return self._zero_fallback()
        if len(tokens) == 1:
            return self._one_fallback(tokens[0])
        
        return self._two_fallback((tokens[-2], tokens[-1]))

    def evaluate(self, path_to_file: str) -> float:
        cnt = 0
        hit_cnt = 0
        with open(path_to_file, "r") as file:
            for line in file:
                tokens = ["<BOS>"] + line.split() + ["<EOS>"]
                for i in range(1, len(tokens)):
                    predicted = self.predict_next(tokens[:i])
                    if predicted == tokens[i]:
                        hit_cnt += 1
                    print(f"REAL: {tokens[i]}, PREDICTED: {predicted}")
                cnt += (len(tokens) - 1)
        return(hit_cnt / cnt)

In [23]:
# Markov model to predict next token type

markov_for_types = MarkovModel()

for walk_obj in os.walk("no_errors_keyword_identifier"):
    folder_name: str = walk_obj[0]
    if folder_name.split("/")[-1] != "without_whitespace":
        continue
    for file_name in walk_obj[2]:
        if file_name.startswith("test") or file_name.startswith("validation"):
            continue

        with open(os.path.join(folder_name, file_name), "r") as file:
            for line in tqdm(file, desc=os.path.join(folder_name, file_name)):
                tokens_types: List[str] = line.split()
                tokens_types = ["<BOS>"] + tokens_types + ["<EOS>"]
                markov_for_types.update(tokens_types)



print(markov_for_types.evaluate("no_errors_keyword_identifier/WikiSQL/tokens_types/without_whitespace/test.txt"))
                

no_errors_keyword_identifier/Clickhouse/tokens_types/without_whitespace/dataset_tests_pr_60095.txt: 0it [00:00…

no_errors_keyword_identifier/Spider/tokens_types/without_whitespace/train.txt: 0it [00:00, ?it/s]

no_errors_keyword_identifier/WikiSQL/tokens_types/without_whitespace/train.txt: 0it [00:00, ?it/s]

no_errors_keyword_identifier/KaggleDBQA/tokens_types/without_whitespace/GreaterManchesterCrime.txt: 0it [00:00…

no_errors_keyword_identifier/KaggleDBQA/tokens_types/without_whitespace/WorldSoccerDataBase.txt: 0it [00:00, ?…

...

no_errors_keyword_identifier/KaggleDBQA/tokens_types/without_whitespace/Pesticide.txt: 0it [00:00, ?it/s]

no_errors_keyword_identifier/KaggleDBQA/tokens_types/without_whitespace/WhatCDHipHop.txt: 0it [00:00, ?it/s]

no_errors_keyword_identifier/KaggleDBQA/tokens_types/without_whitespace/USWildFires.txt: 0it [00:00, ?it/s]

no_errors_keyword_identifier/KaggleDBQA/tokens_types/without_whitespace/StudentMathScore.txt: 0it [00:00, ?it/…

REAL: KeyWord, PREDICTED: KeyWord
REAL: Identifier, PREDICTED: KeyWord
REAL: KeyWord, PREDICTED: KeyWord
REAL: KeyWord, PREDICTED: Identifier
REAL: KeyWord, PREDICTED: Identifier
REAL: Identifier, PREDICTED: Identifier
REAL: Equals, PREDICTED: KeyWord
REAL: Identifier, PREDICTED: Number
REAL: Identifier, PREDICTED: OpeningRoundBracket
REAL: <EOS>, PREDICTED: Comma
REAL: KeyWord, PREDICTED: KeyWord
REAL: Identifier, PREDICTED: KeyWord
REAL: Slash, PREDICTED: KeyWord
REAL: Identifier, PREDICTED: Identifier
REAL: Identifier, PREDICTED: Equals
REAL: KeyWord, PREDICTED: Comma
REAL: KeyWord, PREDICTED: Identifier
REAL: KeyWord, PREDICTED: Identifier
REAL: Identifier, PREDICTED: Identifier
REAL: KeyWord, PREDICTED: KeyWord
REAL: Identifier, PREDICTED: Identifier
REAL: Equals, PREDICTED: KeyWord
REAL: Number, PREDICTED: Number
REAL: Minus, PREDICTED: Comma
REAL: Number, PREDICTED: Number
REAL: <EOS>, PREDICTED: ClosingRoundBracket
REAL: KeyWord, PREDICTED: KeyWord
REAL: Identifier, PREDICTED: 

In [16]:
markov_for_types.predict_next("<BOS>".split())

'KeyWord'

In [9]:
print(markov_for_types.evaluate("no_errors_keyword_identifier/WikiSQL/tokens_types/without_whitespace/test.txt"))

0.0737284114600137


In [45]:
markov_for_types.predict_next("OpeningRoundBracket Identifier".split())

'ClosingRoundBracket'

In [29]:
orb_idx = markov_for_types.token2idx["OpeningRoundBracket"]
ident_idx = markov_for_types.token2idx["Identifier"]
crb_idx = markov_for_types.token2idx["ClosingRoundBracket"]
kw_idx = markov_for_types.token2idx["KeyWord"]
markov_for_types.abs_cnt[kw_idx]
markov_for_types.three_grams_cnt.shape

(485, 42)

In [ ]:
# Markov model to predict KeyWord

In [ ]:
# Markov model to predict Identifier